In [146]:
import os, sys
import rospkg, rosbag
import numpy as np
import tf
import pandas as pd

# Create a RosPack object
rospack = rospkg.RosPack()

# Get the path to the package this script is in
package_path = rospack.get_path('hri_predict_ros')

# Define the path to the bag directory
bag_dir = os.path.join(package_path, 'logs', 'bag')

# Define the path to the plots directory
plot_dir = os.path.join(package_path, 'plots')
if not os.path.exists(plot_dir):
    os.makedirs(plot_dir)

bag_file = os.path.join(bag_dir, 'test_offline_simple_sub_101.bag')

# Specify which topics to read from the rosbag file
topic_names = [
    '/offline/zed/zed_node/body_trk/skeletons',
    '/offline/tf',
]

n_kpts = 18
TF_world_camera = [0.100575, -0.9304, 2.31042, 0.180663, 0.516604, 0.119341, 0.828395]

translation_world_camera = np.array(TF_world_camera[0:3])
quaternion_world_camera = np.array(TF_world_camera[3:7])

# Convert the quaternion to a rotation matrix
rotation_matrix_world_camera = tf.transformations.quaternion_matrix(quaternion_world_camera)

# Create a translation matrix
translation_matrix_world_camera = tf.transformations.translation_matrix(translation_world_camera)

# Combine the rotation and translation to get the transformation matrix from the world frame to the camera frame
cam_to_world_matrix = tf.transformations.concatenate_matrices(
    translation_matrix_world_camera,
    rotation_matrix_world_camera
)

human_meas_names = ['human_kp{}_{}'.format(i, suffix)
                    for i in range(n_kpts)
                    for suffix in ['x', 'y', 'z']]
tcp_meas_names = ['tcp_pos']

Import measurements from bag file

In [147]:
with rosbag.Bag(bag_file, 'r') as bag:
    rows_list = []
    for topic, msg, t in bag.read_messages(topics=topic_names):
        row_dict = {}

        timestamp = t.to_sec()

        human_meas = np.full((1, n_kpts*3), np.nan)
        if topic == '/offline/zed/zed_node/body_trk/skeletons':
            skeleton_kpts = np.full((n_kpts, 3), np.nan)
            if msg.objects:                
                for obj in msg.objects:
                    # Extract skeleton keypoints from message ([x, y, z] for each kpt)
                    kpts = np.array([[kp.kp] for kp in obj.skeleton_3d.keypoints])
                    kpts = kpts[:n_kpts] # select only the first n_kpts

                    skeleton_kpts = np.reshape(kpts, (n_kpts, 3)) # reshape to (n_kpts, 3)

                    # Convert keypoints to world frame
                    for i in range(n_kpts):
                        # Create a homogeneous coordinate for the keypoint position
                        kpt = np.array([skeleton_kpts[i][0],
                                        skeleton_kpts[i][1],
                                        skeleton_kpts[i][2],
                                        1])

                        # Transform the keypoint to the world frame using the transformation matrix
                        kpt_world = np.dot(cam_to_world_matrix, kpt)

                        skeleton_kpts[i][0] = kpt_world[0]
                        skeleton_kpts[i][1] = kpt_world[1]
                        skeleton_kpts[i][2] = kpt_world[2]
                
            else:
                skeleton_kpts = np.full(skeleton_kpts.shape, np.nan)

            # Update current human measurement vector
            human_meas = skeleton_kpts.flatten()

        tcp_meas = np.full((1, 1), np.nan)
        if topic == '/offline/tf':
            for tf_msg in msg.transforms:
                if tf_msg.child_frame_id == 'tool0_controller':
                    tcp_pos = tf_msg.transform.translation
                    tcp_meas = np.array([-tcp_pos.x])

        row_dict.update({'timestamp': timestamp})
        row_dict.update({'human_meas': human_meas.flatten()})
        row_dict.update({'tcp_meas': tcp_meas.flatten()})

        rows_list.append(row_dict)

Store data in a Pandas dataframe

In [148]:
data = pd.DataFrame(rows_list, columns=['timestamp', 'human_meas', 'tcp_meas'])

# split columns into separate columns
for c in data.columns.values:
    data = pd.concat([data, data.pop(c).apply(pd.Series).add_prefix(c+"_")], axis=1)

# change column names
data.columns = ['timestamp'] + human_meas_names + tcp_meas_names

print(data.head(), data.shape)

      timestamp  human_kp0_x  human_kp0_y  human_kp0_z  human_kp1_x   
0  1.717162e+09          NaN          NaN          NaN          NaN  \
1  1.717162e+09          NaN          NaN          NaN          NaN   
2  1.717162e+09          NaN          NaN          NaN          NaN   
3  1.717162e+09          NaN          NaN          NaN          NaN   
4  1.717162e+09          NaN          NaN          NaN          NaN   

   human_kp1_y  human_kp1_z  human_kp2_x  human_kp2_y  human_kp2_z  ...   
0          NaN          NaN          NaN          NaN          NaN  ...  \
1          NaN          NaN          NaN          NaN          NaN  ...   
2          NaN          NaN          NaN          NaN          NaN  ...   
3          NaN          NaN          NaN          NaN          NaN  ...   
4          NaN          NaN          NaN          NaN          NaN  ...   

   human_kp15_x  human_kp15_y  human_kp15_z  human_kp16_x  human_kp16_y   
0           NaN           NaN           NaN    

In [149]:
relative_data = data.copy()

# Make time index relative to the start of the recording
relative_data['timestamp'] = data['timestamp'] - data['timestamp'][0]

# Convert the 'timestamp' column to a TimeDeltaIndex
relative_data['timestamp'] = pd.to_datetime(relative_data['timestamp'], unit='s')

print(relative_data.head())

                      timestamp  human_kp0_x  human_kp0_y  human_kp0_z   
0 1970-01-01 00:00:00.000000000          NaN          NaN          NaN  \
1 1970-01-01 00:00:00.001899480          NaN          NaN          NaN   
2 1970-01-01 00:00:00.003568887          NaN          NaN          NaN   
3 1970-01-01 00:00:00.005044698          NaN          NaN          NaN   
4 1970-01-01 00:00:00.005082607          NaN          NaN          NaN   

   human_kp1_x  human_kp1_y  human_kp1_z  human_kp2_x  human_kp2_y   
0          NaN          NaN          NaN          NaN          NaN  \
1          NaN          NaN          NaN          NaN          NaN   
2          NaN          NaN          NaN          NaN          NaN   
3          NaN          NaN          NaN          NaN          NaN   
4          NaN          NaN          NaN          NaN          NaN   

   human_kp2_z  ...  human_kp15_x  human_kp15_y  human_kp15_z  human_kp16_x   
0          NaN  ...           NaN           NaN        

In [150]:
# Resample the DataFrame to a known frequency
dt = 0.01
freq_str = f'{dt}S' # seconds
resampled_data = relative_data.resample(freq_str, on='timestamp').mean()

print(resampled_data.head())

                         human_kp0_x  human_kp0_y  human_kp0_z  human_kp1_x   
timestamp                                                                     
1970-01-01 00:00:00.000          NaN          NaN          NaN          NaN  \
1970-01-01 00:00:00.010          NaN          NaN          NaN          NaN   
1970-01-01 00:00:00.020          NaN          NaN          NaN          NaN   
1970-01-01 00:00:00.030          NaN          NaN          NaN          NaN   
1970-01-01 00:00:00.040          NaN          NaN          NaN          NaN   

                         human_kp1_y  human_kp1_z  human_kp2_x  human_kp2_y   
timestamp                                                                     
1970-01-01 00:00:00.000          NaN          NaN          NaN          NaN  \
1970-01-01 00:00:00.010          NaN          NaN          NaN          NaN   
1970-01-01 00:00:00.020          NaN          NaN          NaN          NaN   
1970-01-01 00:00:00.030          NaN          NaN  

In [163]:
# Compute the velocity and acceleration of the TCP
resampled_data['tcp_vel'] = resampled_data['tcp_pos'].diff() / dt
resampled_data['tcp_acc'] = resampled_data['tcp_vel'].diff() / dt

# Filter the acceleration to remove noise
resampled_data['tcp_acc'] = resampled_data['tcp_acc'].rolling(window=20).mean()

print(resampled_data.head())

                         human_kp0_x  human_kp0_y  human_kp0_z  human_kp1_x   
timestamp                                                                     
1970-01-01 00:00:00.000          NaN          NaN          NaN          NaN  \
1970-01-01 00:00:00.010          NaN          NaN          NaN          NaN   
1970-01-01 00:00:00.020          NaN          NaN          NaN          NaN   
1970-01-01 00:00:00.030          NaN          NaN          NaN          NaN   
1970-01-01 00:00:00.040          NaN          NaN          NaN          NaN   

                         human_kp1_y  human_kp1_z  human_kp2_x  human_kp2_y   
timestamp                                                                     
1970-01-01 00:00:00.000          NaN          NaN          NaN          NaN  \
1970-01-01 00:00:00.010          NaN          NaN          NaN          NaN   
1970-01-01 00:00:00.020          NaN          NaN          NaN          NaN   
1970-01-01 00:00:00.030          NaN          NaN  

In [153]:
import plotly.express as px

fig = px.line(resampled_data.reset_index(), x=resampled_data.index, y=['tcp_pos'])
fig.add_scatter(x=resampled_data.index, y=resampled_data['human_kp4_y'], mode='markers', name='human_kp4_y', marker=dict(size=3))

fig.update_layout(title='human_kp4_y and tcp over time', xaxis_title='Timestamp', yaxis_title='Value')

# No need to format x-axis ticks as they are already in the desired format
fig.update_xaxes(nticks=10, tickformat='%H:%M:%S')

fig.show()

In [212]:
from filterpy.kalman import UnscentedKalmanFilter, MerweScaledSigmaPoints
from filterpy.kalman import IMMEstimator
from filterpy.common import Q_discrete_white_noise
from scipy.linalg import block_diag
import copy

dt = 0.01
n_kpts = 1 # 18
n_var_per_dof = 3           # position, velocity, acceleration
n_dim_per_kpt = 1 # 3       # x, y, z
var_r = 0.0025
var_q = 0.01
init_P = 1.0

dim_x = n_var_per_dof * n_dim_per_kpt * n_kpts # 3D (position, velocity, acceleration) for each keypoint
dim_z = n_dim_per_kpt * n_kpts # 3D position for each keypoint

p_idx = np.arange(0, dim_x, n_var_per_dof)

# Measurment vector
zs = resampled_data['human_kp4_y']

# Find first element in zs that is not NaN
first_valid_idx = zs.first_valid_index()

t = resampled_data.index[0]
t_end = resampled_data.index[-1]
t_incr = pd.Timedelta(seconds=dt)

# measurement function: only the position is measured
def hx(x):
    return x[p_idx]

sigmas = MerweScaledSigmaPoints(n=dim_x, alpha=.1, beta=2., kappa=1.)

# CONSTANT ACCELERATION UKF
F_block_ca = np.array([[1, dt, 0.5*dt**2],
                       [0, 1, dt],
                       [0, 0, 1]])
F_ca = block_diag(*[F_block_ca for _ in range(n_dim_per_kpt * n_kpts)])

# state transition function: const acceleration
def fx_ca(x, dt):
    return np.dot(F_ca, x)

ca_ukf = UnscentedKalmanFilter(dim_x=dim_x, dim_z=dim_z, dt=dt, hx=hx, fx=fx_ca, points=sigmas)
ca_ukf.x = np.nan * np.ones(dim_x)
ca_ukf.P = np.eye(dim_x) * init_P
ca_ukf.R = var_r
ca_ukf.Q = Q_discrete_white_noise(dim=n_var_per_dof, dt=dt, var=var_q, block_size=n_dim_per_kpt)

ca_ufk_initialized = False
uxs_ca = []

# CONSTANT ACCELERATION UKF WITH NO PROCESS ERROR
ca_no_ukf = copy.deepcopy(ca_ukf)
ca_no_ukf.Q = np.zeros((dim_x, dim_x))

# CONSTANT VELOCITY UKF
F_block_cv = np.array([[1, dt, 0],
                       [0, 1, 0],
                       [0, 0, 0]])
F_cv = block_diag(*[F_block_cv for _ in range(n_dim_per_kpt * n_kpts)])

# state transition function: const velocity
def fx_cv(x, dt):
    return np.dot(F_cv, x)

cv_ukf = UnscentedKalmanFilter(dim_x=dim_x, dim_z=dim_z, dt=dt, hx=hx, fx=fx_cv, points=sigmas)
cv_ukf.x = np.nan * np.ones(dim_x)
cv_ukf.P = np.eye(dim_x) * init_P
cv_ukf.R = var_r
cv_ukf.Q = Q_discrete_white_noise(dim=n_var_per_dof, dt=dt, var=var_q, block_size=n_dim_per_kpt)

ufk_initialized = False
uxs_cv = []




# Initialize IMM estimator
# filters = [copy.deepcopy(ca_ukf), ca_no_ukf, copy.deepcopy(cv_ukf)]
filters = [copy.deepcopy(ca_ukf), ca_no_ukf]

# Columns imm estimator
col_names_imm = ['imm_pos', 'imm_vel', 'imm_acc']
# col_names_prob_imm = ['prob_ca', 'prob_ca_no', 'prob_cv']
col_names_prob_imm = ['prob_ca', 'prob_ca_no']

# Transition matrix
# M = np.array([[0.85, 0.10, 0.05],
#               [0.75, 0.15, 0.10],
#               [0.50, 0.30, 0.20]])
# mu = np.array([0.45, 0.30, 0.25])
M = np.array([[0.97, 0.03],
              [0.03, 0.97]])
mu = np.array([0.45, 0.55])

bank = IMMEstimator(filters, mu, M)
uxs_bank, probs_bank = [], []

while t <= t_end:
    if t == first_valid_idx:
        ca_ukf.x = np.array([zs[t], 0.0, 0.0]) # initial state = first measurement
        cv_ukf.x = np.array([zs[t], 0.0, 0.0])
        for f in bank.filters:
            f.x = np.array([zs[t], 0.0, 0.0])
        ufk_initialized = True

    if ufk_initialized:
        ca_ukf.predict()
        cv_ukf.predict()
        bank.predict()
        if not np.isnan(zs[t]):
            ca_ukf.update(zs[t])
            cv_ukf.update(zs[t])
            bank.update(zs[t])
        
    uxs_ca.append(ca_ukf.x.copy())
    uxs_cv.append(cv_ukf.x.copy())
    uxs_bank.append(bank.x.copy())
    probs_bank.append(bank.mu.copy())
    t += t_incr

uxs_ca = np.array(uxs_ca)
uxs_cv = np.array(uxs_cv)
uxs = np.concatenate((uxs_ca, uxs_cv), axis=1)

uxs_bank = np.array(uxs_bank)
probs_bank = np.array(probs_bank)

# Create a DataFrame with the filtered data
filtered_data = pd.DataFrame(uxs, index=resampled_data.index, columns=['ca_pos', 'ca_vel', 'ca_acc', 'cv_pos', 'cv_vel', 'cv_acc'])
imm_data = pd.DataFrame(uxs_bank, index=resampled_data.index, columns=col_names_imm)
imm_probs = pd.DataFrame(probs_bank, index=resampled_data.index, columns=col_names_prob_imm)

In [213]:
fig = px.line(resampled_data.reset_index(), x=resampled_data.index, y=['tcp_pos'])
fig.add_scatter(x=resampled_data.index, y=resampled_data['human_kp4_y'], mode='markers', name='human_kp4_y', marker=dict(size=4))
fig.add_scatter(x=resampled_data.index, y=uxs_ca[:, 0], mode='lines', name='UKF CA Position')
fig.add_scatter(x=resampled_data.index, y=uxs_cv[:, 0], mode='lines', name='UKF CV Position')
fig.add_scatter(x=resampled_data.index, y=uxs_bank[:, 0], mode='lines', name='IMM Position')

fig.update_layout(title='human_kp4_y and tcp over time', xaxis_title='Timestamp', yaxis_title='Value')

# No need to format x-axis ticks as they are already in the desired format
fig.update_xaxes(nticks=10, tickformat='%H:%M:%S')

fig.show()

In [214]:
fig = px.line(resampled_data.reset_index(), x=resampled_data.index, y=['tcp_vel'])
fig.add_scatter(x=resampled_data.index, y=uxs_ca[:, 1], mode='lines', name='UKF CA Velocity')
fig.add_scatter(x=resampled_data.index, y=uxs_cv[:, 1], mode='lines', name='UKF CV Velocity')
fig.add_scatter(x=resampled_data.index, y=uxs_bank[:, 1], mode='lines', name='IMM Velocity')

fig.update_layout(title='human_kp4_y and tcp over time', xaxis_title='Timestamp', yaxis_title='Value')

# No need to format x-axis ticks as they are already in the desired format
fig.update_xaxes(nticks=10, tickformat='%H:%M:%S')

fig.show()

In [187]:
fig = px.line(resampled_data.reset_index(), x=resampled_data.index, y=['tcp_acc'])
fig.add_scatter(x=resampled_data.index, y=uxs_ca[:, 2], mode='lines', name='UKF CA Acceleration')
fig.add_scatter(x=resampled_data.index, y=uxs_cv[:, 2], mode='lines', name='UKF CV Acceleration')
fig.add_scatter(x=resampled_data.index, y=uxs_bank[:, 2], mode='lines', name='IMM Acceleration')

fig.update_layout(title='human_kp4_y and tcp over time', xaxis_title='Timestamp', yaxis_title='Value')

# No need to format x-axis ticks as they are already in the desired format
fig.update_xaxes(nticks=10, tickformat='%H:%M:%S')

fig.show()